# Прогнозирование стоимости автомобиля

## Загрузка данных и библиотек

In [1]:
import os
# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

#Этот блок нужен только на Kaggle
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# #Этот блок нужен только на локальной машине
# print(os.listdir('./data'))
# PATH_to_file = './data/'

/kaggle/input/sf-dst-car-price-prediction/sample_submission.csv
/kaggle/input/sf-dst-car-price-prediction/test.csv
/kaggle/input/parsing-all-moscow-auto-ru-09-09-2020/all_auto_ru_09_09_2020.csv


In [2]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
import re

import warnings
warnings.filterwarnings('ignore')

import pandas_profiling
from pandas_profiling import ProfileReport

%matplotlib inline

!pip freeze > requirements.txt

RANDOM_SEED = 42

In [3]:
DIR_TEST = '../input/sf-dst-car-price-prediction/'
DIR_TRAIN = '../input/parsing-all-moscow-auto-ru-09-09-2020/'
df_train = pd.read_csv(DIR_TRAIN + 'all_auto_ru_09_09_2020.csv') # взял на кагле, спарсить не получилось
df_test = pd.read_csv(DIR_TEST + 'test.csv')
sample_submission = pd.read_csv(DIR_TEST + 'sample_submission.csv')

Предварительный просмотр данных

In [4]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 89378 entries, 0 to 89377
Data columns (total 26 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   bodyType              89377 non-null  object 
 1   brand                 89378 non-null  object 
 2   color                 89378 non-null  object 
 3   fuelType              89378 non-null  object 
 4   modelDate             89377 non-null  float64
 5   name                  89377 non-null  object 
 6   numberOfDoors         89377 non-null  float64
 7   productionDate        89378 non-null  int64  
 8   vehicleConfiguration  89377 non-null  object 
 9   vehicleTransmission   89377 non-null  object 
 10  engineDisplacement    89377 non-null  object 
 11  enginePower           89377 non-null  float64
 12  description           86124 non-null  object 
 13  mileage               89378 non-null  int64  
 14  Комплектация          89378 non-null  object 
 15  Привод             

In [5]:
df_train.sample(4)

bodyType     brand   color fuelType  modelDate  \
20052              Седан      FORD  040001   бензин     2005.0   
9675   Внедорожник 5 дв.       BMW  040001   дизель     2018.0   
88631    Универсал 5 дв.  MERCEDES  CACECB   дизель     1984.0   
10468  Внедорожник 5 дв.       BMW  040001   бензин     2006.0   

                             name  numberOfDoors  productionDate  \
20052           1.6 MT (115 л.с.)            4.0            2006   
9675   30d 3.0d AT (249 л.с.) 4WD            5.0            2020   
88631       250 2.5d MT (90 л.с.)            5.0            1987   
10468   48i 4.8 AT (355 л.с.) 4WD            5.0            2006   

                vehicleConfiguration vehicleTransmission  ...  Руль  \
20052           SEDAN MECHANICAL 1.6          MECHANICAL  ...  LEFT   
9675   ALLROAD_5_DOORS AUTOMATIC 30d           AUTOMATIC  ...  LEFT   
88631   WAGON_5_DOORS MECHANICAL 250          MECHANICAL  ...  LEFT   
10468  ALLROAD_5_DOORS AUTOMATIC 48i           AUTOMATIC  ...  LEFT   

       Состояние Владельцы        ПТС Таможня Владение      price  \
20052        NaN       3.0  DUPLICATE    True      NaN   275000.0   
9675         NaN       NaN   ORIGINAL    True      NaN  4772400.0   
88631        NaN       3.0   ORIGINAL    True      NaN   110000.0   
10468        NaN       2.0   ORIGINAL    True      NaN   615000.0   

                 start_date  hidden  model  
20052  2020-08-18T08:04:09Z     NaN  FOCUS  
9675   2020-08-11T12:54:33Z     NaN     X4  
88631  2020-06-05T07:15:47Z     NaN   W124  
10468  2020-07-06T15:48:59Z     NaN     X5  

[4 rows x 26 columns]

In [6]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 34686 entries, 0 to 34685
Data columns (total 32 columns):
 #   Column                Non-Null Count  Dtype 
---  ------                --------------  ----- 
 0   bodyType              34686 non-null  object
 1   brand                 34686 non-null  object
 2   car_url               34686 non-null  object
 3   color                 34686 non-null  object
 4   complectation_dict    6418 non-null   object
 5   description           34686 non-null  object
 6   engineDisplacement    34686 non-null  object
 7   enginePower           34686 non-null  object
 8   equipment_dict        24690 non-null  object
 9   fuelType              34686 non-null  object
 10  image                 34686 non-null  object
 11  mileage               34686 non-null  int64 
 12  modelDate             34686 non-null  int64 
 13  model_info            34686 non-null  object
 14  model_name            34686 non-null  object
 15  name                  34686 non-null

In [7]:
df_test.sample(4)

bodyType       brand  \
31105  внедорожник 5 дв.       SKODA   
14891  внедорожник 5 дв.    INFINITI   
23397              седан  VOLKSWAGEN   
7180   внедорожник 5 дв.       VOLVO   

                                                 car_url    color  \
31105  https://auto.ru/cars/used/sale/skoda/yeti/1100...    белый   
14891  https://auto.ru/cars/used/sale/infiniti/qx70/1...    синий   
23397  https://auto.ru/cars/used/sale/volkswagen/pass...  бежевый   
7180   https://auto.ru/cars/used/sale/volvo/xc60/1101...   чёрный   

                                      complectation_dict  \
31105  {"id":"20764952","name":"Monte Carlo","availab...   
14891  {"id":"20182398","name":"Elegance","available_...   
23397                                                NaN   
7180   {"id":"4733681","name":"Премиум Плюс","availab...   

                                             description engineDisplacement  \
31105  Комплектация "Monte-Carlo"\nОтличное состояние...            1.8 LTR   
14891  Продам автомобиль Infiniti QX70 куплен в конце...            3.0 LTR   
23397  ● АВТОКРЕДИТ от 2,9%\n● Первоначальный взнос о...            1.8 LTR   
7180   Продам авто в отличном состоянии. Два комплект...            3.0 LTR   

      enginePower                                     equipment_dict fuelType  \
31105     152 N12  {"cruise-control":true,"tinted-glass":true,"es...   бензин   
14891     238 N12  {"cruise-control":true,"tinted-glass":true,"es...   дизель   
23397     152 N12  {"cruise-control":true,"electro-window-back":t...   бензин   
7180      286 N12  {"cruise-control":true,"asr":true,"tinted-glas...   бензин   

       ...           vehicleConfiguration  vehicleTransmission    vendor  \
31105  ...      ALLROAD_5_DOORS ROBOT 1.8     роботизированная  EUROPEAN   
14891  ...  ALLROAD_5_DOORS AUTOMATIC 3.0       автоматическая  JAPANESE   
23397  ...                SEDAN ROBOT 1.8     роботизированная  EUROPEAN   
7180   ...  ALLROAD_5_DOORS AUTOMATIC 3.0       автоматическая  EUROPEAN   

         Владельцы            Владение       ПТС    Привод   Руль  \
31105  2 владельца                 NaN  Оригинал    полный  Левый   
14891   1 владелец  5 лет и 11 месяцев  Оригинал    полный  Левый   
23397  3 или более                 NaN  Оригинал  передний  Левый   
7180   3 или более   4 года и 4 месяца  Оригинал    полный  Левый   

                Состояние     Таможня  
31105  Не требует ремонта  Растаможен  
14891  Не требует ремонта  Растаможен  
23397  Не требует ремонта  Растаможен  
7180   Не требует ремонта  Растаможен  

[4 rows x 32 columns]

Подготовка данных

In [8]:
df_train['color'] = df_train['color'].map(
    {'CACECB': 'серебристый', 'FAFBFB': 'белый', 'EE1D19': 'красный', '97948F': 'серый',
      '660099': 'пурпурный', '040001': 'чёрный', '4A2197': 'фиолетовый',
      '200204': 'коричневый', '0000CC': 'синий', '007F00': 'зелёный', 'C49648': 'бежевый',
      '22A0F8': 'голубой', 'DEA522': 'золотистый', 'FFD600': 'жёлтый', 'FF8649': 'оранжевый',
      'FFC0CB': 'розовый'})

df_train['vehicleTransmission'] = df_train['vehicleTransmission'].map(
    {'AUTOMATIC': 'автоматическая', 'MECHANICAL': 'механическая', 'VARIATOR': 'вариатор', 
     'ROBOT': 'роботизированная'})

df_train['Руль'] = df_train['Руль'].map({'LEFT': 'левый', 'RIGHT': 'правый'})

# Объединяем трейн и тест в один датасет
df_train['sample'] = 1  # помечаем трейн
df_test['sample'] = 0  # помечаем тест
df_test['price'] = 0

data = df_test.append(df_train, sort=False).reset_index(drop=True)  # объединяем
data = data[~data.price.isnull()]  # убираем строки None для price
data = data[~data.bodyType.isnull()]  # убираем лишние строки

# Приводим колонки к нижнем регистру
for col in data.select_dtypes(include='object').columns:
    data[col][~data[col].isnull()] = data[col][~data[col].isnull()].apply(lambda x: str(x).lower())
    
brands = list(map(lambda x: str.lower(x), df_test.brand.value_counts().index))
data = data[data['brand'].isin(brands)]

In [9]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 83786 entries, 0 to 123346
Data columns (total 38 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   bodyType              83786 non-null  object 
 1   brand                 83786 non-null  object 
 2   car_url               34686 non-null  object 
 3   color                 83786 non-null  object 
 4   complectation_dict    6418 non-null   object 
 5   description           82207 non-null  object 
 6   engineDisplacement    83786 non-null  object 
 7   enginePower           83786 non-null  object 
 8   equipment_dict        24690 non-null  object 
 9   fuelType              83786 non-null  object 
 10  image                 34686 non-null  object 
 11  mileage               83786 non-null  int64  
 12  modelDate             83786 non-null  float64
 13  model_info            34686 non-null  object 
 14  model_name            34686 non-null  object 
 15  name              

Разведочный анализ с Pandas profiling

In [10]:
profile = ProfileReport(data)
profile

Предварительный анализ показал: категориальных переменных 27, числов - 8, булевых - 1. Отсутствие дубликатов строк. Наличие пропущенных значений - 31.6%. Наличие корреляции между столбцами Hidden и Price и обратной корреляции между столбцами modelDate и mileage.

Функции

In [11]:
def change_own(row):
    row = str(row)
    if row.find('или более') > -1:
        return 4
    res = re.match('\d+', row)
    if res is None:
        return row
    else:
        return res[0]
    
def mape(y_true, y_pred): 
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs((y_true - y_pred) / y_true) * 100)

Обработка и подготовка данных к моделированию 

In [12]:
data_temp = data.copy()

dummyes = []
#encod = []

# bodyType
data_temp['bodyType'] = data_temp['bodyType'].astype(str).apply(lambda x: None if x.strip() == '' else x)
data_temp['bodyType'] = data_temp['bodyType'].apply(lambda x: 'купе' if x == 'купе-хардтоп' else x)
data_temp['bodyType'] = data_temp['bodyType'].apply(lambda x: 'седан' if x == 'седан-хардтоп' else x)
dummyes.append('bodyType')

# brand
dummyes.append('brand')

data_temp.drop('car_url', axis=1, inplace=True)

# color
dummyes.append('color')

# complectation_dict
data_temp['complectation_dict'].fillna("{'id': '0'}", inplace=True)
data_temp['complectation_dict'] = data_temp['complectation_dict'].apply(lambda x: len(x))

# description
data_temp['description'].fillna('[]', inplace=True)
# Вводим новые признаки
data_temp['description_word'] = data_temp['description'].apply(lambda x: [i for i in x.split()])
data_temp['salon'] = data_temp['description_word'].apply(lambda x: 1 if ('рольф' or 'панавто' or 'дилер' or 'кредит' or 'обмен' or 'скид' or 'trade-in' or 'выгода' or 'работаем для вас' or 'автосалон' or 'ликвидация') in x else 0)
data_temp['torg'] = data_temp['description_word'].apply(lambda x: 1 if ('торг') in x else 0)
data_temp['leather'] = data_temp['description_word'].apply(lambda x: 1 if ('темный' and 'салон') in x else 0)
data_temp['carter'] = data_temp['description_word'].apply(lambda x: 1 if ('защита' and 'картера') in x else 0)
data_temp['ABS'] = data_temp['description_word'].apply(lambda x: 1 if ('антиблокировочная' and 'система') in x else 0)
data_temp['airbags'] = data_temp['description_word'].apply(lambda x: 1 if ('подушки' and 'безопасности') in x else 0)
data_temp['immob'] = data_temp['description_word'].apply(lambda x: 1 if ('иммобилайзер') in x else 0)
data_temp['central_locking'] = data_temp['description_word'].apply(lambda x: 1 if ('центральный' and 'замок') in x else 0)
data_temp['on_board_computer'] = data_temp['description_word'].apply(lambda x: 1 if ('бортовой' and 'компьютер') in x else 0)
data_temp['cruise_control'] = data_temp['description_word'].apply(lambda x: 1 if ('круиз-контроль') in x else 0)
data_temp['climat_control'] = data_temp['description_word'].apply(lambda x: 1 if ('климат-контроль') in x else 0)
data_temp['multi_rudder'] = data_temp['description_word'].apply(lambda x: 1 if ('мультифункциональный' and 'руль') in x else 0)
data_temp['power_steering'] = data_temp['description_word'].apply(lambda x: 1 if ('гидроусилитель' or 'гидро' or 'усилитель' and 'руля') in x else 0)
data_temp['light_and_rain_sensors'] = data_temp['description_word'].apply(lambda x: 1 if ('датчики' and 'света' and 'дождя') in x else 0)
data_temp['сarbon_body_kits'] = data_temp['description_word'].apply(lambda x: 1 if ('карбоновые' and 'обвесы') in x else 0)
data_temp['rear_diffuser_rkp'] = data_temp['description_word'].apply(lambda x: 1 if ('задний' and 'диффузор') in x else 0)
data_temp['door_closers'] = data_temp['description_word'].apply(lambda x: 1 if ('доводчики' and 'дверей') in x else 0)
data_temp['rear_view_camera'] = data_temp['description_word'].apply(lambda x: 1 if ('камера' or 'видеокамера' and 'заднего' and 'вида') in x else 0)
data_temp['amg'] = data_temp['description_word'].apply(lambda x: 1 if ('amg') in x else 0)
data_temp['bi_xenon_headlights'] = data_temp['description_word'].apply(lambda x: 1 if ('биксеноновые' and 'фары') in x else 0)
data_temp['alloy_wheels'] = data_temp['description_word'].apply(lambda x: 1 if ('легкосплавные' or 'колесные' or 'диски') in x else 0)
data_temp['parking_sensors'] = data_temp['description_word'].apply(lambda x: 1 if ('парктроник' or 'парктронник') in x else 0)
data_temp['dents'] = data_temp['description_word'].apply(lambda x: 1 if ('вмятины' or 'вмятина' or 'царапина' or 'царапины' or 'трещина') in x else 0)
data_temp['roof_with_panoramic_view'] = data_temp['description_word'].apply(lambda x: 1 if ('панорамная' and 'крыша') in x else 0)
data_temp.drop(['description', 'description_word'], axis=1, inplace=True)

# engineDisplacement
data_temp.drop('engineDisplacement', axis=1, inplace=True)

# enginePower
data_temp.drop('enginePower', axis=1, inplace=True)

# model
data_temp.drop('model', axis=1, inplace=True)

#start_date
data_temp.drop('start_date', axis=1, inplace=True)

#Комплектация#####
data_temp.drop('Комплектация', axis=1, inplace=True)

# equipment_dict
data_temp['equipment_dict'].fillna("{}", inplace=True)
data_temp['equipment_dict'] = data_temp['equipment_dict'].apply(lambda x: len(x))

# fuelType
dummyes.append('fuelType')

# image
data_temp['image'].fillna(data_temp['image'].value_counts().index[0], inplace=True)
data_temp['image'] = data_temp['image'].apply(lambda x: 1 if 'avatars' in x else 0)

# model_info
data_temp['model_info'].fillna('{}', inplace=True)
data_temp['model_info'] = data_temp['model_info'].apply(lambda x: len(x))

# model_name
data_temp.drop('model_name', axis=1, inplace=True)

# name
data_temp.drop('name', axis=1, inplace=True)

# parsing_unixtime
data_temp.drop('parsing_unixtime', axis=1, inplace=True)

# priceCurrency
data_temp.drop('priceCurrency', axis=1, inplace=True)

# sell_id
data_temp['sell_id'].fillna(0, inplace=True)
data_temp['sell_id'] = data_temp['sell_id'].astype('float64')

# super_gen  
data_temp.drop('super_gen', axis=1, inplace=True)

# vehicleConfiguration
data_temp.drop(['vehicleConfiguration'], axis=1, inplace=True)
                           
# vehicleTransmission
dummyes.append('vehicleTransmission')

# vendor
vendors = {'ford': 'american', 'hyundai': 'korean', 'nissan': 'japanese', 'peugeot': 'european', 'porsche': 'european', 'renault': 'european', 'skoda': 'european', 'toyota': 'japanese', 'volkswagen': 'european',
           'volvo': 'european', 'great_wall': 'chinese', 'land_rover': 'european', 'mercedes': 'european'}
data_temp['vendor'].fillna(data['brand'].map(vendors), inplace=True)
dummyes.append('vendor')

# hidden
data_temp.drop(['hidden'], axis=1, inplace=True)

# Владельцы
data_temp['Владельцы'].fillna('0', inplace=True)
data_temp['Владельцы'] = data_temp['Владельцы'].apply(change_own).astype('int64')

# Владение
data_temp.drop('Владение', axis=1, inplace=True)

# ПТС
data_temp['ПТС'].fillna('оригинал', inplace=True)
data_temp['ПТС'] = data_temp['ПТС'].apply(lambda x: 'оригинал' if x in ['original', 'оригинал'] else 'дубликат')
dummyes.append('ПТС')

# Привод
data_temp['Привод'].fillna('передний', inplace=True)
dummyes.append('Привод')

# Руль
data_temp['Руль'].fillna('левый', inplace=True) 
dummyes.append('Руль')

# Состояние
data_temp.drop('Состояние', axis=1, inplace=True)

# Таможня
data_temp.drop('Таможня', axis=1, inplace=True)

# price
data_temp['price'] = np.log(data_temp['price'] + 1)

In [13]:
# dummy
for column in dummyes:
    data_temp = pd.get_dummies(data_temp, columns=[column], prefix=col)

Моделирование

In [14]:
train_data = data_temp.query('sample == 1').drop(['sample'], axis=1)

In [15]:
train_data.isna().sum()

complectation_dict    0
equipment_dict        0
image                 0
mileage               0
modelDate             0
                     ..
model_задний          0
model_передний        0
model_полный          0
model_левый           0
model_правый          0
Length: 181, dtype: int64

In [16]:
train_data.sample(4)

complectation_dict  equipment_dict  image  mileage  modelDate  \
119350                  11               2      1        0     2019.0   
82590                   11               2      1   121000     2009.0   
43364                   11               2      1        0     2019.0   
111462                  11               2      1   260000     2007.0   

        model_info  numberOfDoors  productionDate  sell_id  Владельцы  ...  \
119350           2            5.0            2020      0.0          0  ...   
82590            2            5.0            2012      0.0          3  ...   
43364            2            5.0            2020      0.0          0  ...   
111462           2            4.0            2008      0.0          3  ...   

        model_роботизированная  model_european  model_japanese  \
119350                       1               1               0   
82590                        0               0               1   
43364                        0               0               0   
111462                       0               1               0   

        model_дубликат  model_оригинал  model_задний  model_передний  \
119350               0               1             0               0   
82590                0               1             0               1   
43364                0               1             0               0   
111462               0               1             0               1   

        model_полный  model_левый  model_правый  
119350             1            1             0  
82590              0            1             0  
43364              1            1             0  
111462             0            1             0  

[4 rows x 181 columns]

In [17]:
X = train_data.drop(['price'], axis=1)
y = train_data['price']

In [18]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, shuffle=True, random_state=RANDOM_SEED)

In [19]:
# проверяем
train_data.shape, train_data.shape, X.shape, X_train.shape, X_test.shape

((49100, 181), (49100, 181), (49100, 180), (39280, 180), (9820, 180))

In [20]:
model = RandomForestRegressor(n_estimators=300, verbose=1, n_jobs=-1, random_state=RANDOM_SEED)
model.fit(X_train, y_train)

y_pred = model.predict(X_test)

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Done  42 tasks      | elapsed:    7.8s
[Parallel(n_jobs=-1)]: Done 192 tasks      | elapsed:   34.7s
[Parallel(n_jobs=-1)]: Done 300 out of 300 | elapsed:   53.9s finished
[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.1s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    0.3s
[Parallel(n_jobs=4)]: Done 300 out of 300 | elapsed:    0.4s finished


In [21]:
y_test = np.round(np.exp(y_test))
y_pred = np.round(np.exp(y_pred))

print(f'MAPE: {np.round(mape(y_test,y_pred),5)}')

MAPE: 14.79017


    Submission

In [22]:
X_sub = data_temp.query('sample == 0').drop(['sample', 'price'], axis=1)

predict_submission = model.predict(X_sub)

predict_submission = np.round(np.exp(predict_submission))

sample_submission['price'] = predict_submission
sample_submission.to_csv(f'submission.csv', index=False)
sample_submission.head(10)

[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  42 tasks      | elapsed:    0.2s
[Parallel(n_jobs=4)]: Done 192 tasks      | elapsed:    0.7s
[Parallel(n_jobs=4)]: Done 300 out of 300 | elapsed:    1.1s finished


sell_id      price
0  1100575026   622288.0
1  1100549428   942662.0
2  1100658222   767366.0
3  1100937408   700482.0
4  1101037972   745935.0
5  1100912634   572315.0
6  1101228730   573207.0
7  1100165896   381057.0
8  1100768262  1909704.0
9  1101218501  1479011.0